In [1]:
%load_ext autoreload
%autoreload 2

In [6]:
# LOAD
from utils import FILES, load_data, to_full_data

data = load_data(FILES)
full_data = to_full_data(data)
data

{'md': [Document(page_content="# Mode secours (aussi appelé mode dégradé)\n## Passage en mode secours\nVous détectez que la téléphonie est passée en mode secours parce que le bandeau de communication SI-SAMU ne fonctionne plus. L'ordinateur affiche un message qui en précise l'origine. Dans cet exemple, le Session Server est inaccessible. Si vous en avez la possibilité, prenez une photo de l'écran avant de fermer le portail SI-SAMU. Quand la téléphonie est en mode secours vous devez alors utiliser le téléphone positionné sur le bureau. \n\n## Réaction du SAMU au passage en mode secours\nLorsque la téléphonie passe en mode secours, le référent ou responsable du SAMU appelle le support N1 et déclare la panne téléphonique. Il faudra ensuite suivre les consignes du support N3 et, avant de vous déconnecter, vérifiez que vous avez bien accès à votre annuaire téléphonique. Une version Excel de l'annuaire est présente dans la bibliothèque. Le support N3 de l'Agence du numérique en santé ouvre u

In [7]:
# SPLIT
from utils import split_MD_then_recursive

all_splits = split_MD_then_recursive(data)
all_splits

[Document(page_content='67  12. Fonctionnement en mode dégradé  En cas de défaillance du bandeau de communication ou du service de distribution des appels (présenté au chapitre 6) ou d’isolation du site locale (ex : panne d’accès réseau), la brique de téléphonie (ACD de secours du marché M1) prend le relai de la distribution des appels.   Dans ce cas, l’ensemble des actions liées à la téléphonie (modification du statut de l’agent, action téléphonique de type transfert, conférence, etc.) se font depuis le téléphone de', metadata={'source': 'resources/SI-Samu_Documentation_produit_SF4_J18HF2_20231219 - mode secours seul.pdf', 'page': 0}),
 Document(page_content='conférence, etc.) se font depuis le téléphone de l’agent, et plus depuis le bandeau, celui-ci étant inactif ou inaccessible.', metadata={'source': 'resources/SI-Samu_Documentation_produit_SF4_J18HF2_20231219 - mode secours seul.pdf', 'page': 0}),
 Document(page_content="Figure 4. Vue de l'écran du poste téléphonique avec notammen

In [8]:
# EMBED
# Find the relevant splits to then submit those to the model
# -> Create embeddings and store them in a vector database
# -> Use Ollama directly to instantiate an embedding model (ChromaDB here for a vector database)
from langchain_community.embeddings import HuggingFaceInferenceAPIEmbeddings
from langchain_openai import OpenAIEmbeddings
import os

# HuggingFaceInference | Ref.: https://python.langchain.com/docs/integrations/text_embedding/huggingfacehub#hugging-face-inference-api
inference_embeddings = HuggingFaceInferenceAPIEmbeddings(
    api_key=os.environ['HUGGINGFACEHUB_API_TOKEN'], 
    # Good French embedding but doesn't work... | Ref.: https://huggingface.co/dangvantuan/sentence-camembert-large
    model_name="thenlper/gte-large" 
    # "thenlper/gte-large", "sentence-transformers/stsb-xlm-r-multilingual", "sentence-transformers/all-MiniLM-l6-v2", "dangvantuan/sentence-camembert-large"
)

# OpenAI ADA
openai_embeddings = OpenAIEmbeddings()

In [9]:
# RETRIEVE
from utils import get_parent_ensemble_retriever

In [28]:
# PROMPT
from utils import PROMPT

In [31]:
# LLM
# Ref.: https://python.langchain.com/docs/integrations/platforms/openai
from langchain_openai import ChatOpenAI, OpenAI

# OpenAI | Ref.: https://python.langchain.com/docs/integrations/llms/openai
# Pricing | Ref.: https://openai.com/pricing#language-models
gpt35_chat = ChatOpenAI(model_name="gpt-3.5-turbo-1106", temperature=0)
gpt4turbo_chat = ChatOpenAI(model_name="gpt-4-1106-preview", temperature=0)
# print(LLMChain(prompt=prompt, llm=gpt35_chat).run(question))
# print(LLMChain(prompt=prompt, llm=gpt4turbo_chat).run(question))
gpt35 = OpenAI(model_name="gpt-3.5-turbo-1106")
gpt4turbo = OpenAI(model_name="gpt-4-1106-preview")

# Ollama
from utils import mistral, mixtral, llama2, MIXTRAL, MISTRAL, LLAMA2

In [32]:
# PARAMS
llm = mistral
embeddings = openai_embeddings # openai_embeddings, inference_embeddings
k = 5
retriever = get_parent_ensemble_retriever(
    embeddings, 
    full_data, 
    all_splits,
    k, 
    2000, 
    400, 
    "ada-store"
)

In [33]:
from langchain.chains import RetrievalQA

qachain = RetrievalQA.from_chain_type(
    llm=llm, 
    retriever=retriever,
    return_source_documents=True,
    verbose=True,
    chain_type_kwargs={"prompt": PROMPT}
)

In [34]:
def answer_queries(qachain):
    answers = []
    for query in [
        "Comment faire pour me connecter ?",
        "Comment savoir si j'ai des appels en attente ?",
        "Comment faire un transfert accompagné ?",
        "Quel est mon mot de passe pour me connecter au téléphone ?",
        "Dois-je déconnecter mes T2 ?",
        "Quelle est la météo aujourd'hui ?",
        "Quelle est la hauteur de la tour Eiffel ?"
    ]:
        answer = qachain({"query": query})
        answers.append(answer)
        print(f">> {query}\n>> {answer['result']}\n\n")
    return answers

In [35]:
answers = answer_queries(qachain)



> Entering new RetrievalQA chain...
 Pour se connecter au téléphone, vous devez appuyer sur le bouton "logon". Ensuite, saissez votre identifiant de téléphonie personnel qui commence par le chiffre 2 suivi du numéro de votre département. Saisissez ensuite quatre fois zéro quand un mot de passe est demandé sur le téléphone. Enfin, choisissez votre Groupe de Traitement d'Appel (GTA) en utilisant les flèches de navigation du clavier.
> Finished chain.
>> Comment faire pour me connecter ?
>>  Pour se connecter au téléphone, vous devez appuyer sur le bouton "logon". Ensuite, saissez votre identifiant de téléphonie personnel qui commence par le chiffre 2 suivi du numéro de votre département. Saisissez ensuite quatre fois zéro quand un mot de passe est demandé sur le téléphone. Enfin, choisissez votre Groupe de Traitement d'Appel (GTA) en utilisant les flèches de navigation du clavier.




> Entering new RetrievalQA chain...
 Vous pouvez savoir si vous avez des appels en attente en regardan

In [36]:
from utils import parse_answer
list(map(parse_answer, answers))

>> Comment faire pour me connecter ?
>>  Pour se connecter au téléphone, vous devez appuyer sur le bouton "logon". Ensuite, saissez votre identifiant de téléphonie personnel qui commence par le chiffre 2 suivi du numéro de votre département. Saisissez ensuite quatre fois zéro quand un mot de passe est demandé sur le téléphone. Enfin, choisissez votre Groupe de Traitement d'Appel (GTA) en utilisant les flèches de navigation du clavier.
>> Sources :
>>>  > Mode secours (aussi appelé mode dégradé) > Transferts > Transfert accompagné [B25]: ### Transfert accompagné
Vous pouvez également choisir de faire un transfert accompagné. Pour transférer mon appel en l'accompagnant, cliquez sur nouvel appel. Après avoir composé le numéro ou choisi une salle d'attente, attendez que votre correspondant décroche. Lorsque votre correspondant décroche, vous êtes en communication avec lui.
- Vous pouvez ensuite faire la conférence à 3 en ajoutant l'appelant à la conversation en appuyant sur le bouton confé

[None, None, None, None, None, None, None]